In [1]:
import time
import math
import warnings
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import talib as ta
from model import Company, StockLog, IndexLog, PerformanceLog
from model import start_engine
from datetime import date, datetime

%matplotlib inline
warnings.filterwarnings("ignore")

In [2]:
engine = start_engine()

In [6]:
# get all companies
engine = start_engine()
start = datetime.strptime('2008-07-01', '%Y-%m-%d').date()
start = np.datetime64(start)
companies = Company().query().all()

In [9]:
def update_last_ticks(companies='all', engine=engine):
    CSV = 'https://www.alphavantage.co/query?function=TIME_SERIES_INTRADAY'\
          '&interval=1min'\
          '&outputsize=full'\
          '&datatype=csv'\
          '&apikey=B2S8XKGQNA9PKVS0'\
          '&symbol='
    
    if not engine:
        engine = start_engine()
    
    if companies == 'all':
        companies = Company().query().all()
    else:
        company_list = []
        for code in companies:
            company_list.append(Company().query().get(code))
        companies = company_list

    for company in companies:
        stock = company.code
        print('Updating', stock)
        df = pd.read_csv(CSV + stock + '.AX', parse_dates=['timestamp'])
        df['timestamp'] = df['timestamp'].dt.tz_localize('Australia/Sydney')
        df['timestamp'] = df['timestamp'].dt.tz_convert(None)
        df['timestamp'] = df['timestamp'] + pd.Timedelta(days=1)
        df = df.loc[df['timestamp'].idxmax()]
        company.last_dt = df['timestamp'].to_pydatetime()
        company.last_tick = df['close']
        company.save()
        time.sleep(15)

In [10]:
update_last_ticks(companies='all')

Updating ALU
Updating AWC
Updating AMC
Updating AMP
Updating ANN
Updating ANZ
Updating APA
Updating ALL
Updating ASX
Updating AST
Updating BOQ
Updating BEN
Updating BHP
Updating BSL
Updating BLD
Updating BXB
Updating CTX
Updating CGF
Updating CHC
Updating CIM
Updating CWY
Updating CCL
Updating COH
Updating CBA
Updating CPU
Updating CWN
Updating CSL
Updating DXS
Updating DMP
Updating DOW
Updating EVN
Updating FLT
Updating FMG
Updating GMG
Updating GPT
Updating ILU
Updating IPL
Updating IAG
Updating JHX
Updating JHG
Updating JBH
Updating MQG
Updating MFG
Updating MGR
Updating NAB
Updating NCM
Updating NST
Updating OSH
Updating ORI
Updating ORG
Updating OZL
Updating PDL
Updating QAN
Updating QBE
Updating QUB
Updating RHC
Updating REA
Updating RMD
Updating RIO
Updating STO
Updating SEK
Updating SHL
Updating SOL
Updating SGP
Updating SYD
Updating TAH
Updating TLS
Updating TPM
Updating TCL
Updating WES
Updating WBC
Updating WHC
Updating WPL
Updating WOW
Updating WOR
Updating ABC
Updating AGL

In [17]:
table = pd.DataFrame()
for company in companies:
    print('Processing', company.code)
    # get stock data
    CSV = 'https://www.alphavantage.co/query?function=TIME_SERIES_DAILY_ADJUSTED'\
          '&outputsize=full'\
          '&datatype=csv'\
          '&apikey=OW4NZBLAQU5EBFEV'\
          '&symbol=%s' % company.code
    df = pd.read_csv(CSV + '.AX', usecols=[0, 1, 2, 3, 4, 5, 6], parse_dates=['timestamp'])
    df.rename(columns={'timestamp': 'date', 'adjusted_close': 'adj_close', 'close': 'closing', 'open' : 'opening'}, inplace=True)
    df.sort_values(by='date', inplace=True)
    df.set_index('date', inplace=True)
    df.drop(df[df.index < start].index, inplace=True)
    df.drop(df[df.closing == 0].index, inplace=True)
    df['code'] = company.code
    # calculate techincal indicators
    df['change'] = df['closing'].diff(1)
    df['change_pct'] = df['closing'].pct_change(1)
    for period in [15, 50, 200]:
        df['sma%d' % period] = ta.SMA(df['closing'], timeperiod=period)
    for period in [15, 50, 200]:
        df['ema%d' % period] = ta.EMA(df['closing'], timeperiod=period)  
    df['macd'], df['macd_sig'], df['macd_hist']  = ta.MACD(df['closing'], fastperiod=12, slowperiod=26, signalperiod=9)
    df['bb_hi'], df['bb_mid'], df['bb_lo'] = ta.BBANDS(df['closing'], timeperiod=20, nbdevup=2, nbdevdn=2, matype=0)
    df['slowk'], df['slowd'] = ta.STOCH(df['high'], df['low'], df['closing'], fastk_period=14, slowk_period=3, slowk_matype=0, slowd_period=3, slowd_matype=0)
    df['rsi'] = ta.RSI(df['closing'], timeperiod=14)
    df['adx'] = ta.ADX(df['high'], df['low'], df['closing'], timeperiod=14)
    df['cci'] = ta.CCI(df['high'], df['low'], df['closing'], timeperiod=14)
    df['aroon_dn'], df['aroon_up'] = ta.AROON(df['high'], df['low'], timeperiod=25)
    df['chaikin'] = ta.AD(df['high'], df['low'], df['closing'], df['volume'])
    df['obv'] = ta.OBV(df['closing'], df['volume'])
    df['mom'] = ta.MOM(df['closing'], timeperiod=10)
    # read annual reports
    perf_log = PerformanceLog().query().filter(PerformanceLog.company==company)
    fi = pd.read_sql(perf_log.statement, engine)
    fi.set_index('date', inplace=True)
    # Price to EPS Ratio
    eps = fi['eps']
    df = df.merge(eps, how='outer', left_index=True, right_index=True)
    df['eps'].interpolate(method='pad', inplace=True)
    df['pe_ratio'] = df.apply(lambda x: x['closing'] / x['eps'], axis=1)
    df.drop(['eps'], axis=1, inplace=True)
    # Dividend to Price Ratio (Dividend Yield)
    dividend = fi['net_dividend']
    df = df.merge(dividend, how='outer', left_index=True, right_index=True)
    df['net_dividend'].interpolate(method='pad', inplace=True)
    df['dp_ratio'] = df.apply(lambda x: x['net_dividend'] / x['closing'], axis=1)
    df.drop(['net_dividend'], axis=1, inplace=True)    
    # Price to Book Ratio
    bvps = fi['bv_ps']
    df = df.merge(bvps, how='outer', left_index=True, right_index=True)
    df['bv_ps'].interpolate(method='pad', inplace=True)
    df['pb_ratio'] = df.apply(lambda x: x['closing'] / x['bv_ps'], axis=1)
    df.drop(['bv_ps'], axis=1, inplace=True)    
    # clean up
    df.dropna(subset=['opening'], inplace=True)
    table = table.append(df)
    time.sleep(12)
    # write to DB
    # df.set_index('code', append=True, inplace=True) 
    # df.to_sql('test_table', engine, if_exists='append')

Processing WOW
Processing ABC
Processing SYD
Processing IAG
Processing AGL
Processing AWC
Processing ALU
Processing NAB
Processing AMC
Processing AMP
Processing ANN
Processing ANZ
Processing APA
Processing ALL
Processing ASX
Processing AST
Processing BOQ
Processing BEN
Processing BHP
Processing BSL
Processing BLD
Processing BXB
Processing CTX
Processing CGF
Processing CHC
Processing CIM
Processing CWY
Processing CCL
Processing COH
Processing CBA
Processing CPU
Processing CWN
Processing CSL
Processing DXS
Processing DMP
Processing DOW
Processing EVN
Processing FLT
Processing FMG
Processing GMG
Processing GPT
Processing ILU
Processing IPL
Processing JHX
Processing JHG
Processing JBH
Processing MQG
Processing MFG
Processing MGR
Processing NCM
Processing NST
Processing OSH
Processing ORI
Processing ORG
Processing OZL
Processing PDL
Processing QAN
Processing QUB
Processing RHC
Processing REA
Processing RMD
Processing RIO
Processing STO
Processing SEK
Processing SHL
Processing SOL
Processing

In [19]:
table['code'] = table['code'].astype(str)
table['volume'] = table['volume'].astype(np.int64)
table['prediction'] = np.NaN

In [21]:
table.to_csv('all_stock_logs.csv')

In [22]:
final_table = pd.DataFrame()
for idx in sorted(set(table.index)):
    print(idx)
    tmp = table[table.index == idx]
    tmp['rank'] = tmp['change_pct'].rank(ascending=False)
    final_table = final_table.append(tmp)

2008-07-01 00:00:00
2008-07-02 00:00:00
2008-07-03 00:00:00
2008-07-04 00:00:00
2008-07-07 00:00:00
2008-07-08 00:00:00
2008-07-09 00:00:00
2008-07-10 00:00:00
2008-07-11 00:00:00
2008-07-14 00:00:00
2008-07-15 00:00:00
2008-07-16 00:00:00
2008-07-17 00:00:00
2008-07-18 00:00:00
2008-07-21 00:00:00
2008-07-22 00:00:00
2008-07-23 00:00:00
2008-07-24 00:00:00
2008-07-25 00:00:00
2008-07-28 00:00:00
2008-07-29 00:00:00
2008-07-30 00:00:00
2008-07-31 00:00:00
2008-08-01 00:00:00
2008-08-04 00:00:00
2008-08-05 00:00:00
2008-08-06 00:00:00
2008-08-07 00:00:00
2008-08-08 00:00:00
2008-08-11 00:00:00
2008-08-12 00:00:00
2008-08-13 00:00:00
2008-08-14 00:00:00
2008-08-15 00:00:00
2008-08-18 00:00:00
2008-08-19 00:00:00
2008-08-20 00:00:00
2008-08-21 00:00:00
2008-08-22 00:00:00
2008-08-25 00:00:00
2008-08-26 00:00:00
2008-08-27 00:00:00
2008-08-28 00:00:00
2008-08-29 00:00:00
2008-09-01 00:00:00
2008-09-02 00:00:00
2008-09-03 00:00:00
2008-09-04 00:00:00
2008-09-05 00:00:00
2008-09-08 00:00:00


In [47]:
final_table.to_csv('final.csv')

In [21]:
final_table.set_index('code', append=True, inplace=True) 

In [49]:
final_table.head()

code  opening   high    low  closing  adjusted   volume  sma15  \
date                                                                        
2008-07-01  ABC     3.76   3.92   3.71     3.82      2.33  1336038    NaN   
2008-07-01  AGL    13.17  13.35  12.97    13.08      8.14  1113712    NaN   
2008-07-01  ALQ     4.87   4.87   4.81     4.83      1.48   269202    NaN   
2008-07-01  ALU     0.53   0.53   0.53     0.53      0.38     3140    NaN   
2008-07-01  AWC     3.57   3.62   3.55     3.62      2.33  5715227    NaN   

            sma50  sma200  ...       chaikin        obv  mom  pe_ratio  \
date                       ...                                           
2008-07-01    NaN     NaN  ...  6.362086e+04  1336038.0  NaN       NaN   
2008-07-01    NaN     NaN  ... -4.689314e+05  1113712.0  NaN       NaN   
2008-07-01    NaN     NaN  ... -8.973400e+04   269202.0  NaN       NaN   
2008-07-01    NaN     NaN  ...  0.000000e+00     3140.0  NaN       NaN   
2008-07-01    NaN     NaN  ...  5.715227e+06  5715227.0  NaN       NaN   

            dp_ratio  pb_ratio  prediction  rank  change  change_pct  
date                                                                  
2008-07-01       NaN       NaN        None   NaN     NaN         NaN  
2008-07-01       NaN       NaN        None   NaN     NaN         NaN  
2008-07-01       NaN       NaN        None   NaN     NaN         NaN  
2008-07-01       NaN       NaN        None   NaN     NaN         NaN  
2008-07-01       NaN       NaN        None   NaN     NaN         NaN  

[5 rows x 36 columns]

MultiIndex(levels=[[2008-07-01, 2008-07-02, 2008-07-03, 2008-07-04, 2008-07-07, 2008-07-08, 2008-07-09, 2008-07-10, 2008-07-11, 2008-07-14, 2008-07-15, 2008-07-16, 2008-07-17, 2008-07-18, 2008-07-21, 2008-07-22, 2008-07-23, 2008-07-24, 2008-07-25, 2008-07-28, 2008-07-29, 2008-07-30, 2008-07-31, 2008-08-01, 2008-08-04, 2008-08-05, 2008-08-06, 2008-08-07, 2008-08-08, 2008-08-11, 2008-08-12, 2008-08-13, 2008-08-14, 2008-08-15, 2008-08-18, 2008-08-19, 2008-08-20, 2008-08-21, 2008-08-22, 2008-08-25, 2008-08-26, 2008-08-27, 2008-08-28, 2008-08-29, 2008-09-01, 2008-09-02, 2008-09-03, 2008-09-04, 2008-09-05, 2008-09-08, 2008-09-09, 2008-09-10, 2008-09-11, 2008-09-12, 2008-09-15, 2008-09-16, 2008-09-17, 2008-09-18, 2008-09-19, 2008-09-22, 2008-09-23, 2008-09-24, 2008-09-25, 2008-09-26, 2008-09-29, 2008-09-30, 2008-10-01, 2008-10-02, 2008-10-03, 2008-10-05, 2008-10-06, 2008-10-07, 2008-10-08, 2008-10-09, 2008-10-10, 2008-10-12, 2008-10-13, 2008-10-14, 2008-10-15, 2008-10-16, 2008-10-17, 2008-10-

In [35]:
final_table.index

MultiIndex(levels=[[2008-07-01, 2008-07-02, 2008-07-03, 2008-07-04, 2008-07-07, 2008-07-08, 2008-07-09, 2008-07-10, 2008-07-11, 2008-07-14, 2008-07-15, 2008-07-16, 2008-07-17, 2008-07-18, 2008-07-21, 2008-07-22, 2008-07-23, 2008-07-24, 2008-07-25, 2008-07-28, 2008-07-29, 2008-07-30, 2008-07-31, 2008-08-01, 2008-08-04, 2008-08-05, 2008-08-06, 2008-08-07, 2008-08-08, 2008-08-11, 2008-08-12, 2008-08-13, 2008-08-14, 2008-08-15, 2008-08-18, 2008-08-19, 2008-08-20, 2008-08-21, 2008-08-22, 2008-08-25, 2008-08-26, 2008-08-27, 2008-08-28, 2008-08-29, 2008-09-01, 2008-09-02, 2008-09-03, 2008-09-04, 2008-09-05, 2008-09-08, 2008-09-09, 2008-09-10, 2008-09-11, 2008-09-12, 2008-09-15, 2008-09-16, 2008-09-17, 2008-09-18, 2008-09-19, 2008-09-22, 2008-09-23, 2008-09-24, 2008-09-25, 2008-09-26, 2008-09-29, 2008-09-30, 2008-10-01, 2008-10-02, 2008-10-03, 2008-10-05, 2008-10-06, 2008-10-07, 2008-10-08, 2008-10-09, 2008-10-10, 2008-10-12, 2008-10-13, 2008-10-14, 2008-10-15, 2008-10-16, 2008-10-17, 2008-10-

In [27]:
import sqlalchemy.orm as orm
Session = orm.sessionmaker()
Session.configure(bind=engine)
sess = Session()

In [ ]:
sess.bulk_insert_mappings(TestTable, final_table.to_dict(orient="records"))